In [ ]:
import pandas as pd
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter
from datetime import datetime

# Caminhos
arquivo_entrada = '/content/2025-04-01_sigesguarda_-_Base_de_Dados.csv'
arquivo_saida = 'ocorrencias.csv'

# Lê o CSV
df = pd.read_csv(arquivo_entrada, sep=';', encoding='latin1')

# Colunas adicionais obrigatórias
colunas_necessarias = [
    'OCORRENCIA_DATA', 'OCORRENCIA_HORA',
    'LOGRADOURO_NOME', 'ATENDIMENTO_BAIRRO_NOME',
    'NATUREZA1_DESCRICAO', 'SUBCATEGORIA1_DESCRICAO',
    'ORIGEM_CHAMADO_DESCRICAO', 'REGIONAL_FATO_NOME',
    'semana'
]

# Verifica e trata colunas
for col in colunas_necessarias:
    if col in df.columns:
        df[col] = df[col].astype(str).str.strip()
    else:
        df[col] = ''

# Converte data para datetime
df['OCORRENCIA_DATA_DT'] = pd.to_datetime(df['OCORRENCIA_DATA'], format='%d/%m/%Y', errors='coerce')

# Extrai semana ISO e ano
df['semana_iso'] = df['OCORRENCIA_DATA_DT'].dt.isocalendar().week
df['ano'] = df['OCORRENCIA_DATA_DT'].dt.isocalendar().year

# Cria dicionário: (ano, semana) → lista de datas
semana_to_datas = (
    df.groupby(['ano', 'semana_iso'])['OCORRENCIA_DATA']
    .apply(lambda x: ', '.join(sorted(set(x))))
    .to_dict()
)

# Adiciona coluna semana com as datas da mesma semana
df['semana'] = df.apply(lambda row: semana_to_datas.get((row['ano'], row['semana_iso']), ''), axis=1)

# Cria colunas auxiliares
df['time'] = df['OCORRENCIA_DATA'] + ' ' + df['OCORRENCIA_HORA']
df['endereco'] = df['LOGRADOURO_NOME'] + ', ' + df['ATENDIMENTO_BAIRRO_NOME'] + ', Curitiba, Brasil'
df['lat_lon'] = ''

# Metadados
metadados = {
    "time": "Data e hora combinadas da ocorrência",
    "semana": "Lista de datas presentes no dataset que pertencem à mesma semana ISO da ocorrência",
    "lat_lon": "Coordenadas geográficas (latitude e longitude)",
    "endereco": "Endereço completo (logradouro + bairro + cidade)",
    "ATENDIMENTO_BAIRRO_NOME": "Bairro onde ocorreu o atendimento",
    "LOGRADOURO_NOME": "Nome da rua onde ocorreu a ocorrência",
    "OCORRENCIA_DATA": "Data da ocorrência",
    "OCORRENCIA_HORA": "Hora da ocorrência",
    "NATUREZA1_DESCRICAO": "Tipo da ocorrência",
    "SUBCATEGORIA1_DESCRICAO": "Descrição mais específica da ocorrência",
    "ORIGEM_CHAMADO_DESCRICAO": "Canal de origem do chamado",
    "REGIONAL_FATO_NOME": "Regional da prefeitura responsável",
}

# Ordem de colunas de saída
colunas_saida = list(metadados.keys())

# Inicializa geocodificador
locator = Nominatim(user_agent="myGeocoder")
geocode = RateLimiter(locator.geocode, min_delay_seconds=1)

# Escreve cabeçalho e metadados
with open(arquivo_saida, 'w', encoding='utf-8') as f:
    # Cabeçalhos
    f.write(','.join(colunas_saida) + '\n')

    # Linha de metadados (descrições)
    linha_metadados = ['"' + str(metadados.get(col, "")).replace('"', '') + '"' for col in colunas_saida]
    f.write(','.join(linha_metadados) + '\n')

    # Processa e salva linha a linha
    for i in range(len(df)):
        endereco = df.at[i, 'endereco']
        try:
          location = geocode(endereco)
          if location:
              df.at[i, 'lat_lon'] = f"{location.latitude} {location.longitude}"
          else:
              # Tenta com apenas bairro + cidade + país
              bairro = df.at[i, 'ATENDIMENTO_BAIRRO_NOME']
              endereco_bairro = f"{bairro}, Curitiba, Brasil"
              location_bairro = geocode(endereco_bairro)
              if location_bairro:
                  df.at[i, 'lat_lon'] = f"{location_bairro.latitude} {location_bairro.longitude}"
              else:
                  df.at[i, 'lat_lon'] = ''

        except Exception as e:
            print(f"Erro ao geocodificar linha {i}: {e}")
            df.at[i, 'lat_lon'] = ''

        row = df.iloc[i]
        linha = ['"' + str(row.get(col, "")).replace('"', '') + '"' for col in colunas_saida]
        f.write(','.join(linha) + '\n')
        print(f"Linha {i + 1}/{len(df)} salva.")

print(f"\nArquivo salvo com cabeçalhos e metadados em: {arquivo_saida}")






/tmp/ipython-input-1-3514713721.py:11: DtypeWarning: Columns (12,13,15,18) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(arquivo_entrada, sep=';', encoding='latin1')


Linha 1/113095 salva.
Linha 2/113095 salva.
Linha 3/113095 salva.
Linha 4/113095 salva.


Linha 5/113095 salva.


Linha 6/113095 salva.


Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/urllib3/connectionpool.py", line 534, in _make_request
    response = conn.getresponse()
               ^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/urllib3/connection.py", line 516, in getresponse
    httplib_response = super().getresponse()
                       ^^^^^^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/http/client.py", line 1395, in getresponse
    response.begin()
  File "/usr/lib/python3.11/http/client.py", line 325, in begin
    version, status, reason = self._read_status()
                              ^^^^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/http/client.py", line 286, in _read_status
    line = str(self.fp.readline(_MAXLINE + 1), "iso-8859-1")
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/socket.py", line 718, in readinto
    return self._sock.recv_into(b)
           ^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/ssl.py", line

...

Linha 5007/113095 salva.


Linha 5008/113095 salva.


Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/urllib3/connectionpool.py", line 534, in _make_request
    response = conn.getresponse()
               ^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/urllib3/connection.py", line 516, in getresponse
    httplib_response = super().getresponse()
                       ^^^^^^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/http/client.py", line 1395, in getresponse
    response.begin()
  File "/usr/lib/python3.11/http/client.py", line 325, in begin
    version, status, reason = self._read_status()
                              ^^^^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/http/client.py", line 286, in _read_status
    line = str(self.fp.readline(_MAXLINE + 1), "iso-8859-1")
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/socket.py", line 718, in readinto
    return self._sock.recv_into(b)
           ^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/ssl.py", line

Linha 5009/113095 salva.
Linha 5010/113095 salva.
Linha 5011/113095 salva.
Linha 5012/113095 salva.
Linha 5013/113095 salva.
Linha 5014/113095 salva.
Linha 5015/113095 salva.
Linha 5016/113095 salva.
Linha 5017/113095 salva.
Linha 5018/113095 salva.
Linha 5019/113095 salva.
Linha 5020/113095 salva.
Linha 5021/113095 salva.
Linha 5022/113095 salva.
Linha 5023/113095 salva.
Linha 5024/113095 salva.
Linha 5025/113095 salva.
Linha 5026/113095 salva.
Linha 5027/113095 salva.
Linha 5028/113095 salva.
Linha 5029/113095 salva.
Linha 5030/113095 salva.
Linha 5031/113095 salva.
Linha 5032/113095 salva.


KeyboardInterrupt: 

In [ ]:
pip install geopy